In [ ]:
# Import required libraries
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
from scipy import stats
import warnings
warnings.filterwarnings('ignore')

# Set up plotting style
plt.style.use('seaborn-v0_8')
sns.set_palette("husl")
plt.rcParams['figure.figsize'] = (12, 8)
plt.rcParams['font.size'] = 10

# Import our converted trading modules
import sys
import os
sys.path.append(os.path.abspath('..'))

from converted_code.data_loader import load_futures_data, load_stock_data
from converted_code.backshift import backshift
from converted_code.smartmean import smartmean
from converted_code.smartstd import smartstd
from converted_code.calculateReturns import calculateReturns
from converted_code.calculateMaxDD import calculateMaxDD

print("✅ All libraries imported successfully!")
print("📊 Ready for momentum trading analysis")


In [ ]:
# Load Treasury futures data for time series momentum
print("📈 Loading Treasury Futures Data...")
try:
    tu_data = load_futures_data('TU', '20120813')
    tu_prices = tu_data['cl'][:, 0]  # Use first contract
    tu_dates = tu_data['tday']
    print(f"✅ Loaded {len(tu_dates)} days of Treasury futures data")
    print(f"   Date range: {tu_dates[0]} to {tu_dates[-1]}")
    print(f"   Price range: ${tu_prices.min():.2f} to ${tu_prices.max():.2f}")
    
    # Convert dates to pandas datetime for easier handling
    tu_dates_pd = pd.to_datetime(tu_dates.astype(str), format='%Y%m%d')
    
except Exception as e:
    print(f"⚠️  Could not load Treasury data: {e}")
    print("   Using synthetic data for demonstration...")
    
    # Generate synthetic Treasury futures data
    np.random.seed(42)
    n_days = 1000
    tu_dates = np.arange(20100101, 20100101 + n_days)
    tu_dates_pd = pd.to_datetime(tu_dates.astype(str), format='%Y%m%d')
    
    # Generate realistic Treasury futures prices (around 130-140 range)
    returns = np.random.normal(0, 0.008, n_days)  # 0.8% daily volatility
    tu_prices = 135 * np.cumprod(1 + returns)
    
    print(f"✅ Generated {len(tu_dates)} days of synthetic Treasury data")

print(f"\n📊 Treasury Futures Summary:")
print(f"   Mean price: ${tu_prices.mean():.2f}")
print(f"   Volatility: {tu_prices.std():.2f}")
print(f"   Total return: {(tu_prices[-1]/tu_prices[0] - 1)*100:.2f}%")


In [ ]:
# Load stock data for cross-sectional momentum
print("📈 Loading Stock Market Data...")
try:
    stock_data = load_stock_data('20120424')
    stock_prices = stock_data['cl']
    stock_dates = stock_data['tday']
    stock_symbols = stock_data.get('syms', [f'Stock_{i}' for i in range(stock_prices.shape[1])])
    
    print(f"✅ Loaded stock data: {stock_prices.shape[0]} days × {stock_prices.shape[1]} stocks")
    print(f"   Date range: {stock_dates[0]} to {stock_dates[-1]}")
    
    # Convert dates to pandas datetime
    stock_dates_pd = pd.to_datetime(stock_dates.astype(str), format='%Y%m%d')
    
except Exception as e:
    print(f"⚠️  Could not load stock data: {e}")
    print("   Using synthetic data for demonstration...")
    
    # Generate synthetic stock data
    np.random.seed(42)
    n_days = 1000
    n_stocks = 100
    stock_dates = np.arange(20100101, 20100101 + n_days)
    stock_dates_pd = pd.to_datetime(stock_dates.astype(str), format='%Y%m%d')
    
    # Generate correlated stock returns with momentum effects
    base_returns = np.random.normal(0, 0.02, (n_days, n_stocks))
    
    # Add some momentum persistence
    for i in range(1, n_days):
        momentum_factor = 0.1  # 10% momentum persistence
        base_returns[i] += momentum_factor * base_returns[i-1]
    
    # Convert to prices
    stock_prices = 100 * np.cumprod(1 + base_returns, axis=0)
    stock_symbols = [f'Stock_{i:03d}' for i in range(n_stocks)]
    
    print(f"✅ Generated {n_days} days × {n_stocks} stocks of synthetic data")

print(f"\n📊 Stock Market Summary:")
print(f"   Average stock price: ${stock_prices.mean():.2f}")
print(f"   Price volatility: {stock_prices.std():.2f}")
print(f"   Number of stocks: {stock_prices.shape[1]}")

# Create a DataFrame for easier analysis
stock_df = pd.DataFrame(stock_prices, index=stock_dates_pd, columns=stock_symbols[:stock_prices.shape[1]])
print(f"   DataFrame shape: {stock_df.shape}")


In [ ]:
def time_series_momentum_strategy(prices, lookback=250, holddays=25):
    """
    Implement time series momentum strategy.
    
    Parameters:
    -----------
    prices : array-like
        Price series
    lookback : int
        Lookback period for momentum signal (default: 250 days = 1 year)
    holddays : int
        Holding period for positions (default: 25 days = 1 month)
    
    Returns:
    --------
    dict : Strategy results including positions, returns, and metrics
    """
    
    # Generate momentum signals
    # Long when current price > price from lookback days ago
    # Short when current price < price from lookback days ago
    longs = prices > backshift(lookback, prices)
    shorts = prices < backshift(lookback, prices)
    
    # Initialize position array
    positions = np.zeros(len(prices))
    
    # Build positions over holding period to avoid look-ahead bias
    for h in range(holddays):
        long_lag = backshift(h, longs.astype(float))
        long_lag = np.nan_to_num(long_lag, nan=0).astype(bool)
        
        short_lag = backshift(h, shorts.astype(float))
        short_lag = np.nan_to_num(short_lag, nan=0).astype(bool)
        
        positions[long_lag] += 1
        positions[short_lag] -= 1
    
    # Normalize positions by holding period
    positions = positions / holddays
    
    # Calculate market returns
    market_returns = calculateReturns(prices, 1)
    market_returns = np.nan_to_num(market_returns, nan=0)
    
    # Calculate strategy returns
    # Use lagged positions to avoid look-ahead bias
    strategy_returns = backshift(1, positions) * market_returns
    strategy_returns = np.nan_to_num(strategy_returns, nan=0)
    
    # Calculate cumulative returns
    cumulative_returns = np.cumprod(1 + strategy_returns) - 1
    market_cumulative = np.cumprod(1 + market_returns) - 1
    
    # Calculate performance metrics
    valid_returns = strategy_returns[strategy_returns != 0]
    
    if len(valid_returns) > 0:
        annual_return = np.prod(1 + valid_returns) ** (252 / len(valid_returns)) - 1
        volatility = np.std(valid_returns) * np.sqrt(252)
        sharpe_ratio = annual_return / volatility if volatility > 0 else 0
        
        # Maximum drawdown
        max_dd, max_dd_duration = calculateMaxDD(cumulative_returns)
        
        # Win rate
        win_rate = np.sum(valid_returns > 0) / len(valid_returns)
        
        # Number of trades
        position_changes = np.diff(np.concatenate([[0], positions]))
        num_trades = np.sum(np.abs(position_changes) > 0)
        
    else:
        annual_return = volatility = sharpe_ratio = max_dd = max_dd_duration = win_rate = num_trades = 0
    
    return {
        'positions': positions,
        'strategy_returns': strategy_returns,
        'market_returns': market_returns,
        'cumulative_returns': cumulative_returns,
        'market_cumulative': market_cumulative,
        'annual_return': annual_return,
        'volatility': volatility,
        'sharpe_ratio': sharpe_ratio,
        'max_drawdown': max_dd,
        'max_dd_duration': max_dd_duration,
        'win_rate': win_rate,
        'num_trades': num_trades,
        'longs': longs,
        'shorts': shorts
    }

# Run the time series momentum strategy on Treasury futures
print("🚀 Running Time Series Momentum Strategy on Treasury Futures...")
print("=" * 60)

ts_results = time_series_momentum_strategy(tu_prices, lookback=250, holddays=25)

print(f"📊 Time Series Momentum Results:")
print(f"   Annual Return:     {ts_results['annual_return']:8.2%}")
print(f"   Volatility:        {ts_results['volatility']:8.2%}")
print(f"   Sharpe Ratio:      {ts_results['sharpe_ratio']:8.2f}")
print(f"   Max Drawdown:      {ts_results['max_drawdown']:8.2%}")
print(f"   Max DD Duration:   {ts_results['max_dd_duration']:8.0f} days")
print(f"   Win Rate:          {ts_results['win_rate']:8.2%}")
print(f"   Number of Trades:  {ts_results['num_trades']:8.0f}")

# Compare to buy-and-hold
market_annual = np.prod(1 + ts_results['market_returns']) ** (252 / len(ts_results['market_returns'])) - 1
market_vol = np.std(ts_results['market_returns']) * np.sqrt(252)
market_sharpe = market_annual / market_vol if market_vol > 0 else 0

print(f"\n📈 Buy-and-Hold Comparison:")
print(f"   Market Annual Return: {market_annual:8.2%}")
print(f"   Market Volatility:    {market_vol:8.2%}")
print(f"   Market Sharpe Ratio:  {market_sharpe:8.2f}")
print(f"   Strategy Excess Return: {ts_results['annual_return'] - market_annual:8.2%}")


In [ ]:
def cross_sectional_momentum_strategy(prices, lookback=252, holddays=25, top_n=50):
    """
    Implement cross-sectional momentum strategy (Kent Daniel style).
    
    Parameters:
    -----------
    prices : array-like (2D)
        Price matrix (time x assets)
    lookback : int
        Lookback period for momentum calculation (default: 252 days = 1 year)
    holddays : int
        Holding period for positions (default: 25 days = 1 month)
    top_n : int
        Number of top/bottom performers to select (default: 50)
    
    Returns:
    --------
    dict : Strategy results including positions, returns, and metrics
    """
    
    n_days, n_assets = prices.shape
    
    # Calculate returns for momentum ranking
    returns = calculateReturns(prices, 1)
    returns = np.nan_to_num(returns, nan=0)
    
    # Calculate cumulative returns over lookback period for ranking
    cum_returns = np.zeros_like(prices)
    for i in range(lookback, n_days):
        # Calculate cumulative return over lookback period
        period_returns = returns[i-lookback+1:i+1, :]
        cum_returns[i, :] = np.prod(1 + period_returns, axis=0) - 1
    
    # Initialize position matrix
    positions = np.zeros_like(prices)
    
    # Generate trading signals
    for i in range(lookback, n_days):
        # Rank assets by momentum (cumulative returns)
        momentum_scores = cum_returns[i, :]
        
        # Handle NaN values
        valid_scores = ~np.isnan(momentum_scores)
        if np.sum(valid_scores) < 2 * top_n:
            continue
            
        # Get rankings
        rankings = np.argsort(momentum_scores[valid_scores])
        valid_indices = np.where(valid_scores)[0]
        
        # Select top and bottom performers
        if len(rankings) >= 2 * top_n:
            # Bottom performers (short)
            bottom_indices = valid_indices[rankings[:top_n]]
            # Top performers (long)
            top_indices = valid_indices[rankings[-top_n:]]
            
            # Set positions for holding period
            for h in range(min(holddays, n_days - i)):
                if i + h < n_days:
                    positions[i + h, top_indices] = 1.0 / top_n  # Long position
                    positions[i + h, bottom_indices] = -1.0 / top_n  # Short position
    
    # Calculate strategy returns
    strategy_returns = np.sum(backshift(1, positions) * returns, axis=1)
    strategy_returns = np.nan_to_num(strategy_returns, nan=0)
    
    # Calculate market returns (equal-weighted)
    market_returns = np.nanmean(returns, axis=1)
    market_returns = np.nan_to_num(market_returns, nan=0)
    
    # Calculate cumulative returns
    cumulative_returns = np.cumprod(1 + strategy_returns) - 1
    market_cumulative = np.cumprod(1 + market_returns) - 1
    
    # Calculate performance metrics
    valid_returns = strategy_returns[strategy_returns != 0]
    
    if len(valid_returns) > 0:
        annual_return = np.prod(1 + valid_returns) ** (252 / len(valid_returns)) - 1
        volatility = np.std(valid_returns) * np.sqrt(252)
        sharpe_ratio = annual_return / volatility if volatility > 0 else 0
        
        # Maximum drawdown
        max_dd, max_dd_duration = calculateMaxDD(cumulative_returns)
        
        # Win rate
        win_rate = np.sum(valid_returns > 0) / len(valid_returns)
        
        # Number of rebalances
        position_changes = np.sum(np.abs(np.diff(positions, axis=0)), axis=1)
        num_rebalances = np.sum(position_changes > 0)
        
    else:
        annual_return = volatility = sharpe_ratio = max_dd = max_dd_duration = win_rate = num_rebalances = 0
    
    return {
        'positions': positions,
        'strategy_returns': strategy_returns,
        'market_returns': market_returns,
        'cumulative_returns': cumulative_returns,
        'market_cumulative': market_cumulative,
        'annual_return': annual_return,
        'volatility': volatility,
        'sharpe_ratio': sharpe_ratio,
        'max_drawdown': max_dd,
        'max_dd_duration': max_dd_duration,
        'win_rate': win_rate,
        'num_rebalances': num_rebalances,
        'cum_returns': cum_returns
    }

# Run the cross-sectional momentum strategy on stocks
print("🚀 Running Cross-Sectional Momentum Strategy on Stocks...")
print("=" * 60)

# Use a subset of stocks for faster computation if we have many
max_stocks = min(100, stock_prices.shape[1])
cs_results = cross_sectional_momentum_strategy(
    stock_prices[:, :max_stocks], 
    lookback=252, 
    holddays=25, 
    top_n=min(20, max_stocks//4)
)

print(f"📊 Cross-Sectional Momentum Results:")
print(f"   Annual Return:     {cs_results['annual_return']:8.2%}")
print(f"   Volatility:        {cs_results['volatility']:8.2%}")
print(f"   Sharpe Ratio:      {cs_results['sharpe_ratio']:8.2f}")
print(f"   Max Drawdown:      {cs_results['max_drawdown']:8.2%}")
print(f"   Max DD Duration:   {cs_results['max_dd_duration']:8.0f} days")
print(f"   Win Rate:          {cs_results['win_rate']:8.2%}")
print(f"   Number of Rebalances: {cs_results['num_rebalances']:8.0f}")

# Compare to market
cs_market_annual = np.prod(1 + cs_results['market_returns']) ** (252 / len(cs_results['market_returns'])) - 1
cs_market_vol = np.std(cs_results['market_returns']) * np.sqrt(252)
cs_market_sharpe = cs_market_annual / cs_market_vol if cs_market_vol > 0 else 0

print(f"\n📈 Market Comparison:")
print(f"   Market Annual Return: {cs_market_annual:8.2%}")
print(f"   Market Volatility:    {cs_market_vol:8.2%}")
print(f"   Market Sharpe Ratio:  {cs_market_sharpe:8.2f}")
print(f"   Strategy Excess Return: {cs_results['annual_return'] - cs_market_annual:8.2%}")


In [ ]:
# Create comprehensive performance visualization
fig, axes = plt.subplots(2, 2, figsize=(16, 12))
fig.suptitle('Momentum Trading Strategies Performance Analysis', fontsize=16, fontweight='bold')

# 1. Cumulative Returns Comparison
ax1 = axes[0, 0]
ax1.plot(tu_dates_pd[:len(ts_results['cumulative_returns'])], 
         ts_results['cumulative_returns'] * 100, 
         label='Time Series Momentum', linewidth=2, color='blue')
ax1.plot(tu_dates_pd[:len(ts_results['market_cumulative'])], 
         ts_results['market_cumulative'] * 100, 
         label='Buy & Hold (Treasury)', linewidth=2, color='gray', alpha=0.7)
ax1.set_title('Time Series Momentum: Cumulative Returns', fontweight='bold')
ax1.set_ylabel('Cumulative Return (%)')
ax1.legend()
ax1.grid(True, alpha=0.3)

# 2. Cross-sectional momentum cumulative returns
ax2 = axes[0, 1]
ax2.plot(stock_dates_pd[:len(cs_results['cumulative_returns'])], 
         cs_results['cumulative_returns'] * 100, 
         label='Cross-Sectional Momentum', linewidth=2, color='red')
ax2.plot(stock_dates_pd[:len(cs_results['market_cumulative'])], 
         cs_results['market_cumulative'] * 100, 
         label='Market (Equal Weight)', linewidth=2, color='gray', alpha=0.7)
ax2.set_title('Cross-Sectional Momentum: Cumulative Returns', fontweight='bold')
ax2.set_ylabel('Cumulative Return (%)')
ax2.legend()
ax2.grid(True, alpha=0.3)

# 3. Rolling Sharpe Ratio (252-day window)
ax3 = axes[1, 0]
window = 252

# Calculate rolling Sharpe for time series momentum
ts_rolling_sharpe = []
for i in range(window, len(ts_results['strategy_returns'])):
    window_returns = ts_results['strategy_returns'][i-window:i]
    if np.std(window_returns) > 0:
        sharpe = np.mean(window_returns) * np.sqrt(252) / (np.std(window_returns) * np.sqrt(252))
        ts_rolling_sharpe.append(sharpe)
    else:
        ts_rolling_sharpe.append(0)

# Calculate rolling Sharpe for cross-sectional momentum
cs_rolling_sharpe = []
for i in range(window, len(cs_results['strategy_returns'])):
    window_returns = cs_results['strategy_returns'][i-window:i]
    if np.std(window_returns) > 0:
        sharpe = np.mean(window_returns) * np.sqrt(252) / (np.std(window_returns) * np.sqrt(252))
        cs_rolling_sharpe.append(sharpe)
    else:
        cs_rolling_sharpe.append(0)

if len(ts_rolling_sharpe) > 0:
    ax3.plot(tu_dates_pd[window:window+len(ts_rolling_sharpe)], 
             ts_rolling_sharpe, label='Time Series', linewidth=2, color='blue')

if len(cs_rolling_sharpe) > 0:
    ax3.plot(stock_dates_pd[window:window+len(cs_rolling_sharpe)], 
             cs_rolling_sharpe, label='Cross-Sectional', linewidth=2, color='red')

ax3.axhline(y=0, color='black', linestyle='--', alpha=0.5)
ax3.set_title('Rolling Sharpe Ratio (252-day window)', fontweight='bold')
ax3.set_ylabel('Sharpe Ratio')
ax3.legend()
ax3.grid(True, alpha=0.3)

# 4. Return Distribution Comparison
ax4 = axes[1, 1]
ts_valid_returns = ts_results['strategy_returns'][ts_results['strategy_returns'] != 0]
cs_valid_returns = cs_results['strategy_returns'][cs_results['strategy_returns'] != 0]

if len(ts_valid_returns) > 0:
    ax4.hist(ts_valid_returns * 100, bins=50, alpha=0.6, label='Time Series', 
             color='blue', density=True)

if len(cs_valid_returns) > 0:
    ax4.hist(cs_valid_returns * 100, bins=50, alpha=0.6, label='Cross-Sectional', 
             color='red', density=True)

ax4.axvline(x=0, color='black', linestyle='--', alpha=0.5)
ax4.set_title('Daily Returns Distribution', fontweight='bold')
ax4.set_xlabel('Daily Return (%)')
ax4.set_ylabel('Density')
ax4.legend()
ax4.grid(True, alpha=0.3)

plt.tight_layout()
plt.show()

# Print summary statistics
print("\n" + "="*80)
print("📊 MOMENTUM STRATEGIES PERFORMANCE SUMMARY")
print("="*80)

print(f"\n🔵 TIME SERIES MOMENTUM (Treasury Futures):")
print(f"   Annual Return:      {ts_results['annual_return']:8.2%}")
print(f"   Volatility:         {ts_results['volatility']:8.2%}")
print(f"   Sharpe Ratio:       {ts_results['sharpe_ratio']:8.2f}")
print(f"   Max Drawdown:       {ts_results['max_drawdown']:8.2%}")
print(f"   Win Rate:           {ts_results['win_rate']:8.2%}")

print(f"\n🔴 CROSS-SECTIONAL MOMENTUM (Stocks):")
print(f"   Annual Return:      {cs_results['annual_return']:8.2%}")
print(f"   Volatility:         {cs_results['volatility']:8.2%}")
print(f"   Sharpe Ratio:       {cs_results['sharpe_ratio']:8.2f}")
print(f"   Max Drawdown:       {cs_results['max_drawdown']:8.2%}")
print(f"   Win Rate:           {cs_results['win_rate']:8.2%}")

print(f"\n📈 BENCHMARK COMPARISON:")
print(f"   Treasury B&H Return: {market_annual:8.2%}")
print(f"   Stock Market Return: {cs_market_annual:8.2%}")
print(f"   TS Momentum Alpha:   {ts_results['annual_return'] - market_annual:8.2%}")
print(f"   CS Momentum Alpha:   {cs_results['annual_return'] - cs_market_annual:8.2%}")


In [ ]:
def statistical_significance_tests(strategy_returns, market_returns, num_simulations=1000):
    """
    Perform statistical significance tests for momentum strategies.
    
    Parameters:
    -----------
    strategy_returns : array-like
        Strategy returns
    market_returns : array-like  
        Market returns for comparison
    num_simulations : int
        Number of Monte Carlo simulations
        
    Returns:
    --------
    dict : Test results including p-values and statistics
    """
    
    # Remove zero returns for cleaner analysis
    strategy_returns = strategy_returns[strategy_returns != 0]
    market_returns = market_returns[market_returns != 0]
    
    if len(strategy_returns) == 0:
        return {'error': 'No valid strategy returns'}
    
    # 1. Basic t-test (assuming normal distribution)
    strategy_mean = np.mean(strategy_returns)
    strategy_std = np.std(strategy_returns)
    n_obs = len(strategy_returns)
    
    if strategy_std > 0:
        t_stat = strategy_mean * np.sqrt(n_obs) / strategy_std
        p_value_ttest = 2 * (1 - stats.t.cdf(np.abs(t_stat), n_obs - 1))
    else:
        t_stat = p_value_ttest = 0
    
    # 2. Bootstrap test
    bootstrap_means = []
    for _ in range(num_simulations):
        bootstrap_sample = np.random.choice(strategy_returns, size=len(strategy_returns), replace=True)
        bootstrap_means.append(np.mean(bootstrap_sample))
    
    p_value_bootstrap = np.sum(np.array(bootstrap_means) <= 0) / num_simulations
    
    # 3. Randomized market returns test
    if len(market_returns) > 0:
        market_mean = np.mean(market_returns)
        market_std = np.std(market_returns)
        
        random_means = []
        for _ in range(num_simulations):
            # Generate random returns with same statistical properties as market
            random_returns = np.random.normal(market_mean, market_std, len(strategy_returns))
            random_means.append(np.mean(random_returns))
        
        p_value_random_market = np.sum(np.array(random_means) >= strategy_mean) / num_simulations
    else:
        p_value_random_market = np.nan
    
    # 4. Sharpe ratio test
    if strategy_std > 0:
        strategy_sharpe = strategy_mean / strategy_std * np.sqrt(252)
        
        # Bootstrap Sharpe ratios
        bootstrap_sharpes = []
        for _ in range(num_simulations):
            bootstrap_sample = np.random.choice(strategy_returns, size=len(strategy_returns), replace=True)
            if np.std(bootstrap_sample) > 0:
                bootstrap_sharpes.append(np.mean(bootstrap_sample) / np.std(bootstrap_sample) * np.sqrt(252))
        
        if len(bootstrap_sharpes) > 0:
            p_value_sharpe = np.sum(np.array(bootstrap_sharpes) <= 0) / len(bootstrap_sharpes)
        else:
            p_value_sharpe = np.nan
    else:
        strategy_sharpe = p_value_sharpe = 0
    
    return {
        'strategy_mean': strategy_mean,
        'strategy_std': strategy_std,
        'strategy_sharpe': strategy_sharpe,
        't_statistic': t_stat,
        'p_value_ttest': p_value_ttest,
        'p_value_bootstrap': p_value_bootstrap,
        'p_value_random_market': p_value_random_market,
        'p_value_sharpe': p_value_sharpe,
        'n_observations': n_obs
    }

# Test statistical significance for both strategies
print("🧪 STATISTICAL SIGNIFICANCE TESTING")
print("=" * 60)

# Time Series Momentum Tests
print("\n🔵 Time Series Momentum (Treasury Futures):")
ts_tests = statistical_significance_tests(
    ts_results['strategy_returns'], 
    ts_results['market_returns'], 
    num_simulations=1000
)

if 'error' not in ts_tests:
    print(f"   Strategy Mean Return:    {ts_tests['strategy_mean']:8.6f}")
    print(f"   Strategy Std Dev:       {ts_tests['strategy_std']:8.6f}")
    print(f"   Strategy Sharpe Ratio:  {ts_tests['strategy_sharpe']:8.2f}")
    print(f"   T-statistic:            {ts_tests['t_statistic']:8.2f}")
    print(f"   P-value (t-test):       {ts_tests['p_value_ttest']:8.4f}")
    print(f"   P-value (bootstrap):    {ts_tests['p_value_bootstrap']:8.4f}")
    print(f"   P-value (random market): {ts_tests['p_value_random_market']:8.4f}")
    print(f"   P-value (Sharpe):       {ts_tests['p_value_sharpe']:8.4f}")
    print(f"   Number of observations: {ts_tests['n_observations']:8.0f}")
else:
    print(f"   Error: {ts_tests['error']}")

# Cross-Sectional Momentum Tests
print("\n🔴 Cross-Sectional Momentum (Stocks):")
cs_tests = statistical_significance_tests(
    cs_results['strategy_returns'], 
    cs_results['market_returns'], 
    num_simulations=1000
)

if 'error' not in cs_tests:
    print(f"   Strategy Mean Return:    {cs_tests['strategy_mean']:8.6f}")
    print(f"   Strategy Std Dev:       {cs_tests['strategy_std']:8.6f}")
    print(f"   Strategy Sharpe Ratio:  {cs_tests['strategy_sharpe']:8.2f}")
    print(f"   T-statistic:            {cs_tests['t_statistic']:8.2f}")
    print(f"   P-value (t-test):       {cs_tests['p_value_ttest']:8.4f}")
    print(f"   P-value (bootstrap):    {cs_tests['p_value_bootstrap']:8.4f}")
    print(f"   P-value (random market): {cs_tests['p_value_random_market']:8.4f}")
    print(f"   P-value (Sharpe):       {cs_tests['p_value_sharpe']:8.4f}")
    print(f"   Number of observations: {cs_tests['n_observations']:8.0f}")
else:
    print(f"   Error: {cs_tests['error']}")

# Interpretation
print(f"\n📋 INTERPRETATION:")
print(f"   P-values < 0.05 indicate statistical significance at 95% confidence level")
print(f"   P-values < 0.01 indicate statistical significance at 99% confidence level")

# Check significance
if 'error' not in ts_tests:
    ts_significant = ts_tests['p_value_ttest'] < 0.05
    print(f"   Time Series Momentum is {'SIGNIFICANT' if ts_significant else 'NOT SIGNIFICANT'} (p={ts_tests['p_value_ttest']:.4f})")

if 'error' not in cs_tests:
    cs_significant = cs_tests['p_value_ttest'] < 0.05
    print(f"   Cross-Sectional Momentum is {'SIGNIFICANT' if cs_significant else 'NOT SIGNIFICANT'} (p={cs_tests['p_value_ttest']:.4f})")


In [ ]:
def calculate_drawdown_series(cumulative_returns):
    """Calculate drawdown series from cumulative returns."""
    peak = np.maximum.accumulate(cumulative_returns)
    drawdown = (cumulative_returns - peak) / (1 + peak)
    return drawdown

# Calculate drawdown series
ts_drawdown = calculate_drawdown_series(ts_results['cumulative_returns'])
cs_drawdown = calculate_drawdown_series(cs_results['cumulative_returns'])

# Create risk analysis visualization
fig, axes = plt.subplots(2, 2, figsize=(16, 12))
fig.suptitle('Risk Analysis and Drawdown Patterns', fontsize=16, fontweight='bold')

# 1. Drawdown over time
ax1 = axes[0, 0]
ax1.fill_between(tu_dates_pd[:len(ts_drawdown)], ts_drawdown * 100, 0, 
                 alpha=0.6, color='blue', label='Time Series Momentum')
ax1.set_title('Time Series Momentum: Drawdown Over Time', fontweight='bold')
ax1.set_ylabel('Drawdown (%)')
ax1.grid(True, alpha=0.3)
ax1.legend()

ax2 = axes[0, 1]
ax2.fill_between(stock_dates_pd[:len(cs_drawdown)], cs_drawdown * 100, 0, 
                 alpha=0.6, color='red', label='Cross-Sectional Momentum')
ax2.set_title('Cross-Sectional Momentum: Drawdown Over Time', fontweight='bold')
ax2.set_ylabel('Drawdown (%)')
ax2.grid(True, alpha=0.3)
ax2.legend()

# 3. Risk-Return Scatter Plot
ax3 = axes[1, 0]

# Calculate rolling metrics for scatter plot
window = 63  # Quarterly windows
ts_rolling_returns = []
ts_rolling_vols = []
cs_rolling_returns = []
cs_rolling_vols = []

for i in range(window, len(ts_results['strategy_returns']), window//2):
    window_returns = ts_results['strategy_returns'][i-window:i]
    if len(window_returns[window_returns != 0]) > 10:  # Need sufficient data
        ts_rolling_returns.append(np.mean(window_returns) * 252)
        ts_rolling_vols.append(np.std(window_returns) * np.sqrt(252))

for i in range(window, len(cs_results['strategy_returns']), window//2):
    window_returns = cs_results['strategy_returns'][i-window:i]
    if len(window_returns[window_returns != 0]) > 10:  # Need sufficient data
        cs_rolling_returns.append(np.mean(window_returns) * 252)
        cs_rolling_vols.append(np.std(window_returns) * np.sqrt(252))

if len(ts_rolling_returns) > 0:
    ax3.scatter(np.array(ts_rolling_vols) * 100, np.array(ts_rolling_returns) * 100, 
                alpha=0.6, color='blue', s=50, label='Time Series')

if len(cs_rolling_returns) > 0:
    ax3.scatter(np.array(cs_rolling_vols) * 100, np.array(cs_rolling_returns) * 100, 
                alpha=0.6, color='red', s=50, label='Cross-Sectional')

ax3.axhline(y=0, color='black', linestyle='--', alpha=0.5)
ax3.axvline(x=0, color='black', linestyle='--', alpha=0.5)
ax3.set_xlabel('Volatility (%)')
ax3.set_ylabel('Annual Return (%)')
ax3.set_title('Risk-Return Profile (Rolling Windows)', fontweight='bold')
ax3.legend()
ax3.grid(True, alpha=0.3)

# 4. Monthly Returns Heatmap for Time Series Momentum
ax4 = axes[1, 1]

# Create monthly returns for time series momentum
ts_monthly_returns = []
ts_monthly_dates = []

if len(ts_results['strategy_returns']) > 0:
    # Convert to DataFrame for easier resampling
    ts_df = pd.DataFrame({
        'returns': ts_results['strategy_returns'],
        'date': tu_dates_pd[:len(ts_results['strategy_returns'])]
    }).set_index('date')
    
    # Resample to monthly
    monthly_data = ts_df.resample('M').apply(lambda x: (1 + x).prod() - 1)
    
    if len(monthly_data) > 12:  # Need at least a year of data
        # Create year-month matrix
        monthly_data.index = pd.to_datetime(monthly_data.index)
        monthly_data['year'] = monthly_data.index.year
        monthly_data['month'] = monthly_data.index.month
        
        # Pivot to create heatmap data
        heatmap_data = monthly_data.pivot_table(values='returns', index='year', columns='month', fill_value=0)
        
        # Create heatmap
        sns.heatmap(heatmap_data * 100, annot=True, fmt='.1f', cmap='RdYlBu_r', 
                   center=0, ax=ax4, cbar_kws={'label': 'Monthly Return (%)'})
        ax4.set_title('Time Series Momentum: Monthly Returns Heatmap', fontweight='bold')
        ax4.set_xlabel('Month')
        ax4.set_ylabel('Year')
    else:
        ax4.text(0.5, 0.5, 'Insufficient data for\nmonthly heatmap', 
                ha='center', va='center', transform=ax4.transAxes, fontsize=12)
        ax4.set_title('Monthly Returns Heatmap', fontweight='bold')

plt.tight_layout()
plt.show()

# Print detailed risk metrics
print("\n" + "="*80)
print("📊 DETAILED RISK ANALYSIS")
print("="*80)

print(f"\n🔵 TIME SERIES MOMENTUM RISK METRICS:")
print(f"   Maximum Drawdown:       {ts_results['max_drawdown']:8.2%}")
print(f"   Max DD Duration:        {ts_results['max_dd_duration']:8.0f} days")
print(f"   Volatility (Annual):    {ts_results['volatility']:8.2%}")
print(f"   Downside Deviation:     {np.std(ts_results['strategy_returns'][ts_results['strategy_returns'] < 0]) * np.sqrt(252):8.2%}")
print(f"   VaR (95%):             {np.percentile(ts_results['strategy_returns'][ts_results['strategy_returns'] != 0], 5) * 100:8.2f}%")
print(f"   Skewness:              {stats.skew(ts_results['strategy_returns'][ts_results['strategy_returns'] != 0]):8.2f}")
print(f"   Kurtosis:              {stats.kurtosis(ts_results['strategy_returns'][ts_results['strategy_returns'] != 0]):8.2f}")

print(f"\n🔴 CROSS-SECTIONAL MOMENTUM RISK METRICS:")
print(f"   Maximum Drawdown:       {cs_results['max_drawdown']:8.2%}")
print(f"   Max DD Duration:        {cs_results['max_dd_duration']:8.0f} days")
print(f"   Volatility (Annual):    {cs_results['volatility']:8.2%}")
print(f"   Downside Deviation:     {np.std(cs_results['strategy_returns'][cs_results['strategy_returns'] < 0]) * np.sqrt(252):8.2%}")
print(f"   VaR (95%):             {np.percentile(cs_results['strategy_returns'][cs_results['strategy_returns'] != 0], 5) * 100:8.2f}%")
print(f"   Skewness:              {stats.skew(cs_results['strategy_returns'][cs_results['strategy_returns'] != 0]):8.2f}")
print(f"   Kurtosis:              {stats.kurtosis(cs_results['strategy_returns'][cs_results['strategy_returns'] != 0]):8.2f}")

# Calculate Calmar Ratio (Annual Return / Max Drawdown)
ts_calmar = ts_results['annual_return'] / abs(ts_results['max_drawdown']) if ts_results['max_drawdown'] != 0 else 0
cs_calmar = cs_results['annual_return'] / abs(cs_results['max_drawdown']) if cs_results['max_drawdown'] != 0 else 0

print(f"\n📈 RISK-ADJUSTED PERFORMANCE:")
print(f"   Time Series Calmar Ratio:     {ts_calmar:8.2f}")
print(f"   Cross-Sectional Calmar Ratio: {cs_calmar:8.2f}")
print(f"   (Calmar Ratio = Annual Return / Max Drawdown)")


In [ ]:
# Create a comprehensive summary table
summary_data = {
    'Metric': [
        'Annual Return',
        'Volatility', 
        'Sharpe Ratio',
        'Maximum Drawdown',
        'Calmar Ratio',
        'Win Rate',
        'Number of Trades/Rebalances'
    ],
    'Time Series Momentum': [
        f"{ts_results['annual_return']:.2%}",
        f"{ts_results['volatility']:.2%}",
        f"{ts_results['sharpe_ratio']:.2f}",
        f"{ts_results['max_drawdown']:.2%}",
        f"{ts_calmar:.2f}",
        f"{ts_results['win_rate']:.2%}",
        f"{ts_results['num_trades']:.0f}"
    ],
    'Cross-Sectional Momentum': [
        f"{cs_results['annual_return']:.2%}",
        f"{cs_results['volatility']:.2%}",
        f"{cs_results['sharpe_ratio']:.2f}",
        f"{cs_results['max_drawdown']:.2%}",
        f"{cs_calmar:.2f}",
        f"{cs_results['win_rate']:.2%}",
        f"{cs_results['num_rebalances']:.0f}"
    ],
    'Treasury B&H': [
        f"{market_annual:.2%}",
        f"{market_vol:.2%}",
        f"{market_sharpe:.2f}",
        "N/A",
        "N/A",
        "N/A",
        "1"
    ],
    'Stock Market': [
        f"{cs_market_annual:.2%}",
        f"{cs_market_vol:.2%}",
        f"{cs_market_sharpe:.2f}",
        "N/A",
        "N/A",
        "N/A",
        "1"
    ]
}

summary_df = pd.DataFrame(summary_data)
print("📊 COMPREHENSIVE PERFORMANCE SUMMARY")
print("=" * 100)
print(summary_df.to_string(index=False))

print(f"\n\n🎯 KEY INSIGHTS FROM MOMENTUM ANALYSIS:")
print("=" * 80)

print(f"\n1. 📈 PERFORMANCE COMPARISON:")
if ts_results['sharpe_ratio'] > cs_results['sharpe_ratio']:
    better_strategy = "Time Series Momentum"
    better_sharpe = ts_results['sharpe_ratio']
    worse_sharpe = cs_results['sharpe_ratio']
else:
    better_strategy = "Cross-Sectional Momentum"
    better_sharpe = cs_results['sharpe_ratio']
    worse_sharpe = ts_results['sharpe_ratio']

print(f"   • {better_strategy} shows superior risk-adjusted returns")
print(f"   • Sharpe ratio difference: {better_sharpe:.2f} vs {worse_sharpe:.2f}")
print(f"   • Both strategies {'outperform' if min(ts_results['sharpe_ratio'], cs_results['sharpe_ratio']) > max(market_sharpe, cs_market_sharpe) else 'underperform'} their respective benchmarks")

print(f"\n2. 🎲 STATISTICAL SIGNIFICANCE:")
if 'error' not in ts_tests and 'error' not in cs_tests:
    print(f"   • Time Series Momentum p-value: {ts_tests['p_value_ttest']:.4f}")
    print(f"   • Cross-Sectional Momentum p-value: {cs_tests['p_value_ttest']:.4f}")
    
    significant_strategies = []
    if ts_tests['p_value_ttest'] < 0.05:
        significant_strategies.append("Time Series")
    if cs_tests['p_value_ttest'] < 0.05:
        significant_strategies.append("Cross-Sectional")
    
    if significant_strategies:
        print(f"   • Statistically significant strategies: {', '.join(significant_strategies)}")
    else:
        print(f"   • Neither strategy shows statistical significance at 95% confidence")

print(f"\n3. 📉 RISK CHARACTERISTICS:")
print(f"   • Time Series max drawdown: {ts_results['max_drawdown']:.2%}")
print(f"   • Cross-Sectional max drawdown: {cs_results['max_drawdown']:.2%}")
print(f"   • {'Time Series' if ts_results['max_drawdown'] > cs_results['max_drawdown'] else 'Cross-Sectional'} momentum shows higher maximum drawdown")

print(f"\n4. 🔄 TRADING FREQUENCY:")
print(f"   • Time Series: {ts_results['num_trades']:.0f} trades over the period")
print(f"   • Cross-Sectional: {cs_results['num_rebalances']:.0f} rebalances over the period")
print(f"   • Cross-sectional requires more frequent rebalancing")

print(f"\n5. 💡 PRACTICAL IMPLICATIONS:")
print(f"   • Momentum effects {'appear' if any([ts_tests.get('p_value_ttest', 1) < 0.1, cs_tests.get('p_value_ttest', 1) < 0.1]) else 'do not appear'} to be present in the data")
print(f"   • Time series momentum may be easier to implement (fewer trades)")
print(f"   • Cross-sectional momentum requires larger universe of assets")
print(f"   • Both strategies show {'positive' if min(ts_results['annual_return'], cs_results['annual_return']) > 0 else 'negative'} excess returns over the analysis period")

print(f"\n6. 📚 ALIGNMENT WITH ACADEMIC LITERATURE:")
print(f"   • Results {'are consistent' if max(ts_results['sharpe_ratio'], cs_results['sharpe_ratio']) > 0.5 else 'show mixed evidence'} with momentum literature")
print(f"   • Time series momentum (Chapter 7) shows {'strong' if ts_results['sharpe_ratio'] > 1 else 'moderate' if ts_results['sharpe_ratio'] > 0.5 else 'weak'} performance")
print(f"   • Cross-sectional momentum (Chapter 6) shows {'strong' if cs_results['sharpe_ratio'] > 1 else 'moderate' if cs_results['sharpe_ratio'] > 0.5 else 'weak'} performance")

print(f"\n⚠️  IMPORTANT DISCLAIMERS:")
print(f"   • Results may be influenced by synthetic data if real data unavailable")
print(f"   • Past performance does not guarantee future results")
print(f"   • Transaction costs and market impact not included in analysis")
print(f"   • Strategies may be subject to regime changes and crowding effects")

print(f"\n🔬 NEXT STEPS FOR RESEARCH:")
print(f"   • Test strategies across different time periods and market regimes")
print(f"   • Include transaction costs and realistic trading constraints")
print(f"   • Analyze factor exposures and risk decomposition")
print(f"   • Implement portfolio optimization and risk management overlays")
